# Revised baseline based on https://www.medrxiv.org/content/10.1101/2021.10.07.21264416v1.full.pdf

In [ ]:
import pandas as pd
from pandas.core.frame import DataFrame
import numpy as np
from sklearn.preprocessing import OneHotEncoder, LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.utils import column_or_1d
from typing import Tuple, Any, Union
import random
import pickle
import uuid

In [ ]:
##TODO: change directory to cwd if run on colab
%cd /content/drive/MyDrive/Colab Notebooks/vogel
%ls

/content/drive/MyDrive/Colab Notebooks/vogel
 Baseline.ipynb
'Copy of Glycomics_UGA4_Day0Day28.xlsx'
'Copy of Metabolomics_UGA4_D0toDay28.xlsx'
'Copy of metabolomics_UGA4_global_median_normalized_sample_only.quantified.txt'
'Copy of metabolomics_UGA4_untargeted_median_normalized_sample_only.quantified.txt'
'Copy of Proteomics_UGA4_Day0.xlsx'
'Copy of Transcriptomics_UGA4_day0_logCPMcounts.xlsx'
 data.arff
 data_inspect.ipynb
'fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt'
 KNNC2.csv
 KNNC.csv
 LOGR2.csv
 LOGR.csv
 meta.txt
 RFC2.csv
 RFC.csv
 SGDC2.csv
 SGDC_best.pkl
 SGDC.csv
 SVC2.csv
 SVC.csv
 test_examples.csv
 train_examples.csv


In [ ]:
df = pd.read_csv("fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt", sep="\t")  ##TODO: put the name of the file here
pd.set_option('display.max_columns', None)
df.transpose()

0              1     \
Cohort                                          UGA1           UGA1   
ID                                               A10           A100   
Age                                               25             47   
BMI                                            33.71          33.37   
BMI_category                                   Obese          Obese   
Gender                                          Male         Female   
Race                                           White          White   
Comorbidities                                     No             No   
PreVacc_status                         Prevaccinated  Prevaccinated   
PreVacc_status_year                           Year_0         Year_0   
Month_vaccinated                                Jan.           Jan.   
Vaccine_dose                                Standard       Standard   
D0_Titer_H1N1                                    160             20   
D28_Titer_H1N1                                   160             40   
D0_Titer_H3N2                                    640             20   
D28_Titer_H3N2                                   640             40   
D0_Titer_IBV_Yam                                1280             80   
D28_Titer_IBV_Yam                               1280             80   
D0_Titer_IBV_Vic                                 320             10   
D28_Titer_IBV_Vic                                320            160   
Seroconversion_H1N1                                0              1   
Seroconversion_H3N2                              0.0            1.0   
Seroconversion_IBV_Yam                             0              0   
Seroconversion_IBV_Vic                           0.0            4.0   
Composite_seroconversion                         0.0            6.0   
SC_category_H1N1                                None            Low   
SC_category_H3N2                                None            Low   
SC_category_IBV_Yam                             None           None   
SC_category_IBV_Vic                             None           High   
Composite_SC_category                           None            Low   
Serostatus_H1N1                                    1              0   
Serostatus_H3N2                                    1              0   
Serostatus_IBV_Yam                                 1              1   
Serostatus_IBV_Vic                                 1              0   
Num_SeroPos_strains                                4              1   
Baseline_category_Num_SeroPos_strains           High            Low   
Composite_baseline                              35.0           18.0   

                                            2           3          4     \
Cohort                                      UGA1        UGA1       UGA1   
ID                                          A101        A102       A103   
Age                                           30          47         20   
BMI                                        24.99        25.0       22.1   
BMI_category                              Normal  Overweight     Normal   
Gender                                      Male        Male     Female   
Race                                   Non-white       White  Non-white   
Comorbidities                                Yes          No         No   
PreVacc_status                             Naive       Naive      Naive   
PreVacc_status_year                       Year_3      Year_3     Year_3   
Month_vaccinated                            Jan.        Feb.       Jan.   
Vaccine_dose                            Standard    Standard   Standard   
D0_Titer_H1N1                                 20          80         40   
D28_Titer_H1N1                               640         160        640   
D0_Titer_H3N2                                 20          40         40   
D28_Titer_H3N2                               320          80        320   
D0_Titer_IBV_Yam                             160         640         40   

In [ ]:
for column in df:
  print(column, sorted(df[column].unique()))

Cohort ['UGA1', 'UGA2', 'UGA3', 'UGA4', 'UGA5']
ID ['A1', 'A10', 'A100', 'A101', 'A102', 'A103', 'A104', 'A105', 'A106', 'A107', 'A108', 'A109', 'A11', 'A110', 'A111', 'A112', 'A113', 'A114', 'A115', 'A116', 'A118', 'A119', 'A120', 'A122', 'A123', 'A124', 'A125', 'A126', 'A127', 'A128', 'A129', 'A13', 'A130', 'A131', 'A132', 'A133', 'A134', 'A135', 'A136', 'A137', 'A138', 'A139', 'A14', 'A140', 'A141', 'A142', 'A143', 'A144', 'A145', 'A146', 'A147', 'A148', 'A149', 'A15', 'A150', 'A151', 'A152', 'A154', 'A155', 'A156', 'A157', 'A158', 'A16', 'A160', 'A161', 'A162', 'A163', 'A165', 'A166', 'A168', 'A169', 'A17', 'A170', 'A171', 'A172', 'A174', 'A175', 'A176', 'A177', 'A178', 'A179', 'A18', 'A180', 'A181', 'A182', 'A184', 'A185', 'A186', 'A188', 'A19', 'A190', 'A191', 'A192', 'A193', 'A194', 'A195', 'A196', 'A197', 'A199', 'A2', 'A20', 'A200', 'A201', 'A203', 'A204', 'A205', 'A206', 'A207', 'A208', 'A209', 'A21', 'A210', 'A211', 'A212', 'A213', 'A214', 'A215', 'A216', 'A217', 'A218', 'A2

# PreProcessing
Some codes are reorganized for new implementations.

In [ ]:
def split_age_groups(df): #split the dataset based on differen age groups
  return [df.loc[df["Age_dup"]<18], df.loc[df["Age_dup"]>= 18].loc[df["Age_dup"]<65], df.loc[df["Age_dup"] >= 65]]

In [ ]:
class CustomLabelEncoder(LabelEncoder):
  def __init__(self, month_one_hot=True):
      self.month_one_hot = month_one_hot
  def fit(self, y, ordering: list):  # take an ordering list as an argument
      y = column_or_1d(y, warn=True)
      assert set(ordering) == set(pd.Series(y).unique())
      self.classes_ = ordering
      return self


The below cell random splits the data instead of splitting between UGA1-5 and 4.

In [ ]:
def basic_preprocessing2(df, month_one_hot=True, normalize=True, binary_classification=True, drop_none=False):
  df.loc[df["BMI_category"] == "Normal ", "BMI_category"] = "Normal"
  df.loc[df["BMI_category"] == "Obese ", "BMI_category"] = "Obese"
  
  df["BMI_log"] = np.log(df["BMI"])
  df["Age_log"] = np.log(df["Age"])
  df["Age_dup"] = df["Age"]

  def _normalize(data):
      scaler = StandardScaler()
      scaler.fit(data)
      data = scaler.transform(data)
      return data

  if normalize:
    numerical_cols = ["BMI_log", "Age_log", "Age", "BMI","D0_Titer_H1N1","D0_Titer_H3N2", "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic"]
    df[numerical_cols] = _normalize(df[numerical_cols])

  bmi_cat = df["BMI_category"]
  df2 = df.drop("BMI_category", axis=1)
  comorbidities = df["Comorbidities"]
  df2 = df2.drop("Comorbidities", axis=1)
  dose = df["Vaccine_dose"]
  df2 = df2.drop("Vaccine_dose", axis=1)
  month = None
  if not month_one_hot:
    month = df["Month_vaccinated"]
    df2 = df2.drop("Month_vaccinated", axis=1)

  pre_vac = df["PreVacc_status"]
  df2 = df2.drop("PreVacc_status", axis=1)
  pre_vac_year = df["PreVacc_status_year"]
  df2 = df2.drop("PreVacc_status_year", axis=1)
  h1n1 = df["SC_category_H1N1"]
  df2 = df2.drop("SC_category_H1N1", axis=1)
  h3n2 = df["SC_category_H3N2"]
  df2 = df2.drop("SC_category_H3N2", axis=1)
  yam = df["SC_category_IBV_Yam"]
  df2 = df2.drop("SC_category_IBV_Yam", axis=1)
  vic = df["SC_category_IBV_Vic"]
  df2 = df2.drop("SC_category_IBV_Vic", axis=1)
  comp = df["Composite_SC_category"]
  df2 = df2.drop("Composite_SC_category", axis=1)
  base = df["Baseline_category_Num_SeroPos_strains"]
  df2 = df2.drop("Baseline_category_Num_SeroPos_strains", axis=1)

  for i, column in enumerate(df2.select_dtypes(exclude=["number"]).iloc[:,2:].columns):
    temp = pd.get_dummies(df2[column], drop_first=True, prefix=column)
    df = df.drop(column, axis=1)
    if i != 0 :
      x = x.join(temp)
    else:
      x = temp
  
  # mapping from columns to correct ordering
  ordering_dict = {"BMI_category": (bmi_cat, ["Lean", "Normal", "Overweight", "Obese"]),
                 "Comorbidities": (comorbidities, ["No", "Yes"]),
                 "Vaccine_dose": (dose, ["Standard", "High"]),
                 "PreVacc_status": (pre_vac, ["Naive", "Prevaccinated"]),
                 "PreVacc_status_year": (pre_vac_year, ["Year_3", "Year_0"]),
                 "SC_category_H1N1": (h1n1, ["None", "Low", "High"]),
                 "SC_category_H3N2": (h3n2, ["None", "Low", "High"]),
                 "SC_category_IBV_Yam": (yam, ["None", "Low", "High"]),
                 "SC_category_IBV_Vic": (vic, ["None", "Low", "High"]),
                 "Composite_SC_category": (comp, ["None", "Low", "High"]),
                 "Baseline_category_Num_SeroPos_strains": (base, ["Low", "High"])}  
  if not month_one_hot:
    ordering_dict["Month_vaccinated"] = (month, ["Sep.", "Oct.", "Nov.", "Dec.", "Jan.", "Feb."])
  if binary_classification and not drop_none:
    ordering_dict["SC_category_H1N1"][1].pop(0)
    ordering_dict["SC_category_H3N2"][1].pop(0)
    ordering_dict["SC_category_IBV_Yam"][1].pop(0)
    ordering_dict["SC_category_IBV_Vic"][1].pop(0)
    ordering_dict["Composite_SC_category"][1].pop(0)
    h1n1.loc[h1n1 == "None"] = "Low"
    h3n2.loc[h3n2 == "None"] = "Low"
    yam.loc[yam == "None"] = "Low"
    vic.loc[vic == "None"] = "Low"
    comp.loc[comp == "None"] = "Low"

  lencoder = CustomLabelEncoder(month_one_hot)
  for key, value in ordering_dict.items():
    lencoder.fit(value[0], value[1])
    df.loc[:, key] = lencoder.transform(value[0])

  new = df.join(x)
  if drop_none:
    new = new.loc[new["SC_category_H1N1"] != "None"]
  
  test = new.sample(frac=0.2, axis=0)
  test_strip = test.iloc[:,2:]
  train = new.drop(test.index)
  train_strip = train.iloc[:,2:]
  return train_strip, test_strip

In [ ]:
def basic_preprocessing(df, month_one_hot=True, normalize=True, exclude=True, binary_classification=True):
  df.loc[df["BMI_category"] == "Normal ", "BMI_category"] = "Normal"
  df.loc[df["BMI_category"] == "Obese ", "BMI_category"] = "Obese"
  
  df["BMI_log"] = np.log(df["BMI"])
  df["Age_log"] = np.log(df["Age"])
  df["Age_dup"] = df["Age"]

  def _normalize(data):
      scaler = StandardScaler()
      scaler.fit(data)
      data = scaler.transform(data)
      return data

  if normalize:
    numerical_cols = ["BMI_log", "Age_log", "Age", "BMI","D0_Titer_H1N1","D0_Titer_H3N2", "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic"]
    df[numerical_cols] = _normalize(df[numerical_cols])

  bmi_cat = df["BMI_category"]
  df2 = df.drop("BMI_category", axis=1)
  comorbidities = df["Comorbidities"]
  df2 = df2.drop("Comorbidities", axis=1)
  dose = df["Vaccine_dose"]
  df2 = df2.drop("Vaccine_dose", axis=1)
  month = None
  if not month_one_hot:
    month = df["Month_vaccinated"]
    df2 = df2.drop("Month_vaccinated", axis=1)

  pre_vac = df["PreVacc_status"]
  df2 = df2.drop("PreVacc_status", axis=1)
  pre_vac_year = df["PreVacc_status_year"]
  df2 = df2.drop("PreVacc_status_year", axis=1)
  h1n1 = df["SC_category_H1N1"]
  df2 = df2.drop("SC_category_H1N1", axis=1)
  h3n2 = df["SC_category_H3N2"]
  df2 = df2.drop("SC_category_H3N2", axis=1)
  yam = df["SC_category_IBV_Yam"]
  df2 = df2.drop("SC_category_IBV_Yam", axis=1)
  vic = df["SC_category_IBV_Vic"]
  df2 = df2.drop("SC_category_IBV_Vic", axis=1)
  comp = df["Composite_SC_category"]
  df2 = df2.drop("Composite_SC_category", axis=1)
  base = df["Baseline_category_Num_SeroPos_strains"]
  df2 = df2.drop("Baseline_category_Num_SeroPos_strains", axis=1)

  for i, column in enumerate(df2.select_dtypes(exclude=["number"]).iloc[:,2:].columns):
    temp = pd.get_dummies(df2[column], drop_first=True, prefix=column)
    df = df.drop(column, axis=1)
    if i != 0 :
      x = x.join(temp)
    else:
      x = temp
  
  # mapping from columns to correct ordering
  ordering_dict = {"BMI_category": (bmi_cat, ["Lean", "Normal", "Overweight", "Obese"]),
                 "Comorbidities": (comorbidities, ["No", "Yes"]),
                 "Vaccine_dose": (dose, ["Standard", "High"]),
                 "PreVacc_status": (pre_vac, ["Naive", "Prevaccinated"]),
                 "PreVacc_status_year": (pre_vac_year, ["Year_3", "Year_0"]),
                 "SC_category_H1N1": (h1n1, ["None", "Low", "High"]),
                 "SC_category_H3N2": (h3n2, ["None", "Low", "High"]),
                 "SC_category_IBV_Yam": (yam, ["None", "Low", "High"]),
                 "SC_category_IBV_Vic": (vic, ["None", "Low", "High"]),
                 "Composite_SC_category": (comp, ["None", "Low", "High"]),
                 "Baseline_category_Num_SeroPos_strains": (base, ["Low", "High"])}  
  if not month_one_hot:
    ordering_dict["Month_vaccinated"] = (month, ["Sep.", "Oct.", "Nov.", "Dec.", "Jan.", "Feb."])
  if binary_classification:
    ordering_dict["SC_category_H1N1"][1].pop(0)
    ordering_dict["SC_category_H3N2"][1].pop(0)
    ordering_dict["SC_category_IBV_Yam"][1].pop(0)
    ordering_dict["SC_category_IBV_Vic"][1].pop(0)
    ordering_dict["Composite_SC_category"][1].pop(0)
    h1n1.loc[h1n1 == "None"] = "Low"
    h3n2.loc[h3n2 == "None"] = "Low"
    yam.loc[yam == "None"] = "Low"
    vic.loc[vic == "None"] = "Low"
    comp.loc[comp == "None"] = "Low"

  lencoder = CustomLabelEncoder(month_one_hot)
  for key, value in ordering_dict.items():
    lencoder.fit(value[0], value[1])
    df.loc[:, key] = lencoder.transform(value[0])

  new = df.join(x)
  new_UGA4 = new[new.iloc[:,0] == "UGA4"]  # get two versions of the data: UGA4 and full version; drop the ID columns
  new_UGA4_strip = new_UGA4.iloc[:,2:]
  if exclude:
    new = new[new.iloc[:,0] != "UGA4"]
  new_strip = new.iloc[:,2:]
  return new_strip, new_UGA4_strip

In [ ]:
def io_selector(data: DataFrame, 
                input_columns: Union[list, str] = None, # 'all' for all input columns. Used for feature selection
                output_column: str = None, 
                month_one_hot: bool = True,
                split_feature_label=True,
                split_age=False
                ):
  if split_age:
    data_groups = split_age_groups(data)
  else:
    data_groups = [data]
  
  complete_input_columns = ["Age_log", "BMI_log", "BMI_category", "Gender_Male", "Race_White", 
                              "Comorbidities", "PreVacc_status", "PreVacc_status_year", 
                            "Vaccine_dose", "D0_Titer_H1N1", 
                          "D0_Titer_H3N2", "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic"]

  default_input_columns = ["Age_log", "BMI_log", "Gender_Male", "Race_White", "Comorbidities", 
                          "PreVacc_status", "Vaccine_dose",
                          "D0_Titer_H1N1", "D0_Titer_H3N2", "D0_Titer_IBV_Yam", 
                          "D0_Titer_IBV_Vic"]
  name_mapping = {"Gender": ["Gender_Male"], "Race": ["Race_White"]}
  if month_one_hot:
    default_input_columns.extend(["Month_vaccinated_Jan.", "Month_vaccinated_Feb.",
                          "Month_vaccinated_Sep.", "Month_vaccinated_Oct.",
                          "Month_vaccinated_Nov."])
    complete_input_columns.extend(["Month_vaccinated_Jan.", "Month_vaccinated_Feb.",
                          "Month_vaccinated_Sep.", "Month_vaccinated_Oct.",
                          "Month_vaccinated_Nov."])
    name_mapping["Month_vaccinated"] = ["Month_vaccinated_Jan.",
                                      "Month_vaccinated_Feb.",
                                      "Month_vaccinated_Sep.", 
                                      "Month_vaccinated_Oct.", 
                                      "Month_vaccinated_Nov."]
  else:
    default_input_columns.append("Month_vaccinated")
    complete_input_columns.append("Month_vaccinated")
    
                          
  default_output = ["Composite_seroconversion"]

  
  if input_columns is None: 
    input_columns = default_input_columns
  elif input_columns == "all":
    input_columns = complete_input_columns
  else:
    temp = []
    for item in input_columns:
      if item in name_mapping:
        temp.extend(name_mapping[item])
      else:
        temp.append(item)
    input_columns = temp
  if output_column is None:
    output_column = default_output
  
  output_groups = []
  for data in data_groups:
    x = data[input_columns]
    y = data[output_column]
    if not split_feature_label:
      output_groups.append(x.join(y))
    else:
      output_groups.append((x, y))
  return output_groups


In [ ]:
# handles data converting and saving. Use feature_selection_dataset_wrapper if feature selection is needed
def dataset_wrapper(train: DataFrame,
                    test: DataFrame, 
                    input_columns: Union[list,str] = None, 
                    output_column: str = None,
                    save: bool = False,  # whether to save data in cwd
                    name_extension: str = "",  # name extension for file save
                    to_numpy: bool = True,  # whether to convert to numpy, set to false if feature selection is needed
                    split_age=False,
                    split_age_test=False):  # returns X_train, y_train, X_dev, y_dev, X_test, y_test
  train_groups = io_selector(train, input_columns, output_column, split_age=split_age)
  test_groups = io_selector(test, input_columns, output_column, split_age=split_age_test)
  X_trains = []
  y_trains = []
  X_tests = []
  y_tests = []
  for X_train, y_train in train_groups:
    if save:
      X_train.to_csv("X_train_" + name_extension + ".csv", index=False)
      y_train.to_csv("y_train_" + name_extension + ".csv", index=False)

    if to_numpy:
      X_train = X_train.to_numpy()
      y_train = y_train.to_numpy()

    X_trains.append(X_train)
    y_trains.append(y_train)

  for X_test, y_test in test_groups:
    if save:
      
      X_test.to_csv("X_test_" + name_extension + ".csv", index=False)
      y_test.to_csv("y_test_" + name_extension + ".csv", index=False)
    if to_numpy:
      
      X_test = X_test.to_numpy()
      y_test = y_test.to_numpy()
    X_tests.append(X_test)
    y_tests.append(y_test)
  
    
  return X_trains, y_trains, X_tests, y_tests

# Feature selection: our own attempt
* weka api is very not convenient so we are making our own versions using sk learn.
* for all the models we have its own version of learner based feature selection models so that each model can have the best set of features.

In [ ]:
#TODO

# Training

In [ ]:
from sklearn.linear_model import LinearRegression, SGDRegressor, SGDClassifier, LogisticRegression
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.svm import SVC, SVR
from sklearn.neighbors import KNeighborsRegressor, KNeighborsClassifier

def train_wrapper(X_train: np.ndarray,  # dataset
                  y_train: np.ndarray,
                # Universal parameters (one or more models)
                method: str = None,  # model name
                random_state: int = 10,  # random seed
                model_path: str = None,  # path to save the model, no saving if None
                n_jobs: int = -1,  # number of CPUs to use for some models. -1 means all processors
                max_iter: int = 10000,  # max number of iterations for some models, set to -1 for SV to impose no limits 
                class_weight: Union[dict, str] = None,  # weight of each class or balanced
                penalty: str = "l2",  # logistic has the option of no penalty "None"
                C: float = 1.0, # regularization for logistic or SVM
                # Model specific parameters:
                # SGD Regressor/Classifier
                loss: str = "squared_error",
                alpha: float = 0.01,
                l1_ratio: float = 0.15,
                SGD_epsilon: float = 0.1,
                learning_rate: str = "invscaling",
                eta0: float = 1e-2,
                power_t: float = 0.25,
                average: Union[bool, int] = False,
                # KNN Regressor/Classifier
                n_neighbors: int = 5,
                weights: str = "uniform",
                algorithm: str = "brute",
                leaf_size: int = 30,
                p: int = 2,
                metric: Union[str, callable] = "minkowski",
                metric_params: dict = None,
                # Logistic Regression
                dual: bool = False,
                intercept_scaling: float = 1,
                solver: str = "lbfgs",
                multi_class: str = "auto",
                # Random Forest Classifier/Regressor
                n_estimates: int = 100,
                RFC_criterion: str = "gini",
                RFR_criterion: str = "squared_error",
                max_depth: int = None,
                min_sample_split: Union[int, float] = 2,
                min_samples_leaf: Union[int, float] = 1,
                min_weight_fraction_leaf: float = 0.0,
                max_features: Union[str, int, float] = "auto",
                max_leaf_nodes: int = None,
                min_impurity_decrease: float = 0.0,
                bootstrap: bool = True,
                oob_score: bool = True,
                ccp_alpha: float = 0.0,
                max_samples: Union[int,float] = None,
                # SVC/SVR
                kernel: str = "rbf",
                degree: int = 3,
                gamma: str = "scale",
                coef0: float = 0.0,
                shrinking: bool = True,
                probability: bool = False,
                decision_fuction_shape: str = "ovr",
                break_ties: bool = False,
                SVC_epsilon: float = 0.1,
                ):  # returns a trained model
  random.seed(random_state)
  model = LinearRegression()
  if method == "LR":
    model = LinearRegression()
  elif method == "SGDR":
    model = SGDRegressor(loss=loss, penalty=penalty, alpha=alpha, l1_ratio=l1_ratio, max_iter=max_iter, verbose=0, epsilon=SGD_epsilon, random_state=random_state, learning_rate=learning_rate, eta0=eta0, power_t=power_t, average=average)
  elif method == "KNNR":
    model = KNeighborsRegressor(n_neighbors=n_neighbors, weights=weights, algorithm=algorithm, leaf_size=leaf_size, p=p, metric=metric)
  elif method == "SGDC":
    model = SGDClassifier(loss=loss, penalty=penalty, alpha=alpha, l1_ratio=l1_ratio, max_iter=max_iter, verbose=0, epsilon=SGD_epsilon, n_jobs=n_jobs, random_state=random_state, learning_rate=learning_rate, eta0=eta0, power_t=power_t, class_weight=class_weight, average=average)
  elif method == "KNNC":
    model = KNeighborsClassifier(n_neighbors=n_neighbors, weights=weights, algorithm=algorithm, leaf_size=leaf_size, p=p, metric=metric)
  elif method == "LOGR":
    model = LogisticRegression(penalty=penalty, dual=dual, C=C, intercept_scaling=intercept_scaling, class_weight=class_weight, random_state=random_state, solver=solver, max_iter=max_iter, multi_class=multi_class, verbose=1, n_jobs=n_jobs, l1_ratio=l1_ratio)
  elif method == "RFC":
    model = RandomForestClassifier(n_estimators=n_estimates, criterion=RFC_criterion, max_depth=max_depth, min_samples_split=min_sample_split, min_samples_leaf=min_samples_leaf, min_weight_fraction_leaf=min_weight_fraction_leaf, max_features=max_features, max_leaf_nodes=max_leaf_nodes, min_impurity_decrease=min_impurity_decrease, bootstrap=bootstrap, oob_score=oob_score, n_jobs=n_jobs, random_state=random_state, verbose=1, class_weight=class_weight, ccp_alpha=ccp_alpha, max_samples=max_samples)
  elif method == "RFR":
    model = RandomForestRegressor(n_estimators=n_estimates, criterion=RFR_criterion, max_depth=max_depth, min_samples_split=min_sample_split, min_samples_leaf=min_samples_leaf, min_weight_fraction_leaf=min_weight_fraction_leaf, max_features=max_features, max_leaf_nodes=max_leaf_nodes, min_impurity_decrease=min_impurity_decrease, bootstrap=bootstrap, oob_score=oob_score, n_jobs=n_jobs, random_state=random_state, verbose=1, ccp_alpha=ccp_alpha, max_samples=max_samples)
  elif method == "SVC":
    model = SVC(C=C, kernel=kernel, degree=degree, gamma=gamma, coef0=coef0, shrinking=shrinking, probability=probability, class_weight=class_weight, verbose=1, max_iter=max_iter, decision_function_shape=decision_fuction_shape, break_ties=break_ties, random_state=random_state)
  elif method == "SVR":
    model = SVR(kernel=kernel, degree=degree, gamma=gamma, coef0=coef0, C=C, shrinking=shrinking, epsilon=SVC_epsilon, verbose=1, max_iter=max_iter)
  model.fit(X_train,y_train)
  if model_path:
    with open(method + uuid.uuid1()[:6] + ".pkl", "wb") as f:
      pickle.dump(model, f)
  return model

# The following sections are training of different models with normalizing and feature selection with threshold 1 from before.
Threshold means at least how many times a feature is significant within the 10-CV process.
We tried: 1. different models on different age groups; 2) same model with different inference from different age group. Turns out that one model is enough.


In [ ]:
df = pd.read_csv("fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt", sep="\t")  ##TODO: put the name of the file here
train_df, test_df = basic_preprocessing(df, normalize=True)
model_name_list = ["LOGR", "KNNC", "SGDC", "RFC", "SVC"]

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


* Composite_SC_category

In [ ]:
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=True)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.7s finished


LOGR has accuracy  0.9090909090909091 on child
LOGR has accuracy  0.7904624277456648 on adult1
LOGR has accuracy  0.797752808988764 on adult2
KNNC has accuracy  0.8383838383838383 on child
KNNC has accuracy  0.7355491329479769 on adult1
KNNC has accuracy  0.7865168539325843 on adult2
SGDC has accuracy  0.898989898989899 on child
SGDC has accuracy  0.7658959537572254 on adult1
SGDC has accuracy  0.797752808988764 on adult2


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.2s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.1s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.1s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.


RFC has accuracy  0.9090909090909091 on child
RFC has accuracy  0.7890173410404624 on adult1


[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.7865168539325843 on adult2
[LibSVM]SVC has accuracy  0.898989898989899 on child
SVC has accuracy  0.7630057803468208 on adult1
SVC has accuracy  0.797752808988764 on adult2


Without splitting age group

In [ ]:
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=False)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.


LOGR has accuracy  0.8045454545454546 on all age groups
KNNC has accuracy  0.7522727272727273 on all age groups
SGDC has accuracy  0.7840909090909091 on all age groups


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished


RFC has accuracy  0.8022727272727272 on all age groups
[LibSVM]SVC has accuracy  0.7818181818181819 on all age groups


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


without BMI category

In [ ]:
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                   "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=True)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.


LOGR has accuracy  0.898989898989899 on child
LOGR has accuracy  0.7890173410404624 on adult1
LOGR has accuracy  0.797752808988764 on adult2
KNNC has accuracy  0.8484848484848485 on child
KNNC has accuracy  0.7398843930635838 on adult1
KNNC has accuracy  0.8089887640449438 on adult2
SGDC has accuracy  0.898989898989899 on child
SGDC has accuracy  0.7687861271676301 on adult1
SGDC has accuracy  0.797752808988764 on adult2


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.9090909090909091 on child
RFC has accuracy  0.7890173410404624 on adult1
RFC has accuracy  0.7865168539325843 on adult2
[LibSVM]SVC has accuracy  0.898989898989899 on child
SVC has accuracy  0.7630057803468208 on adult1
SVC has accuracy  0.797752808988764 on adult2


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


without splitting age groups

In [ ]:
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                   "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=False)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.


LOGR has accuracy  0.8022727272727272 on all age groups
KNNC has accuracy  0.759090909090909 on all age groups
SGDC has accuracy  0.7863636363636364 on all age groups


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished


RFC has accuracy  0.8022727272727272 on all age groups
[LibSVM]SVC has accuracy  0.7818181818181819 on all age groups


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


three categories

In [ ]:
df_alt = pd.read_csv("fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt", sep="\t")  ##TODO: put the name of the file here
train_df_alt, test_df_alt = basic_preprocessing(df_alt, normalize=True,binary_classification=False)
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df_alt, test_df_alt, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=True)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.1s finished


LOGR has accuracy  0.6262626262626263 on child
LOGR has accuracy  0.5505780346820809 on adult1
LOGR has accuracy  0.4606741573033708 on adult2
KNNC has accuracy  0.5454545454545454 on child
KNNC has accuracy  0.4479768786127168 on adult1
KNNC has accuracy  0.449438202247191 on adult2
SGDC has accuracy  0.6363636363636364 on child
SGDC has accuracy  0.49277456647398843 on adult1
SGDC has accuracy  0.449438202247191 on adult2


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.6060606060606061 on child
RFC has accuracy  0.5158959537572254 on adult1


[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.4606741573033708 on adult2
[LibSVM]SVC has accuracy  0.6262626262626263 on child
SVC has accuracy  0.48554913294797686 on adult1
SVC has accuracy  0.42696629213483145 on adult2


Without splitting age groups

In [ ]:
df_alt = pd.read_csv("fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt", sep="\t")  ##TODO: put the name of the file here
train_df_alt, test_df_alt = basic_preprocessing(df_alt, normalize=True,binary_classification=False)
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df_alt, test_df_alt, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=False)
if len(X_tests) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    for j in range(len(X_tests)):
      print(model_name,"has accuracy ", model.score(X_tests[j], y_tests[j]),  map[j])

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.1s finished


LOGR has accuracy  0.55 on all age groups
KNNC has accuracy  0.4590909090909091 on all age groups
SGDC has accuracy  0.5045454545454545 on all age groups


[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.3s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.5204545454545455 on all age groups
[LibSVM]SVC has accuracy  0.4954545454545455 on all age groups


train on different age groups

In [ ]:
X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=True,
                                                  split_age_test=True)
print(len(X_tests))
if len(X_trains) == 1:
  map = {0: "on all age groups"}
else:
  map = {0: "on child", 1: "on adult1", 2: "on adult2"}
for model_name in model_name_list:
  for i in range(len(X_trains)):
    model = train_wrapper(X_trains[i], y_trains[i], method=model_name)
    
    print(model_name,"has accuracy ", model.score(X_tests[i], y_tests[i]), map[i])

3
LOGR has accuracy  0.898989898989899 on child
LOGR has accuracy  0.7904624277456648 on adult1
LOGR has accuracy  0.7303370786516854 on adult2
KNNC has accuracy  0.7878787878787878 on child
KNNC has accuracy  0.726878612716763 on adult1
KNNC has accuracy  0.7528089887640449 on adult2
SGDC has accuracy  0.898989898989899 on child
SGDC has accuracy  0.7658959537572254 on adult1
SGDC has accuracy  0.7415730337078652 on adult2


/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.0s finished
/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:    0.0s finished
/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py:1479: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l2)
  "(penalty={})".format(self.penalty)
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Pa

RFC has accuracy  0.8888888888888888 on child


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.


RFC has accuracy  0.7846820809248555 on adult1


[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:    0.1s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    0.2s finished
[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


RFC has accuracy  0.7640449438202247 on adult2
[LibSVM]SVC has accuracy  0.898989898989899 on child
[LibSVM]SVC has accuracy  0.7586705202312138 on adult1
[LibSVM]SVC has accuracy  0.7415730337078652 on adult2


# CV
Now we do randomized search cross validation to find the best hyper parameters.
Notice that we are doing random split for train and test.

In [ ]:
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV
from sklearn.linear_model import LinearRegression, SGDRegressor, SGDClassifier, LogisticRegression
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.svm import SVC, SVR
from sklearn.neighbors import KNeighborsRegressor, KNeighborsClassifier


def cv_wrapper(X_train, y_train, method, param_grid, scoring, mode="grid_search"):
  model = None
  if method == "LR":
    model = LinearRegression()
  elif method == "SGDR":
    model = SGDRegressor()
  elif method == "KNNR":
    model = KNeighborsRegressor()
  elif method == "SGDC":
    model = SGDClassifier()
  elif method == "KNNC":
    model = KNeighborsClassifier()
  elif method == "LOGR":
    model = LogisticRegression()
  elif method == "RFC":
    model = RandomForestClassifier()
  elif method == "RFR":
    model = RandomForestRegressor()
  elif method == "SVC":
    model = SVC()
  elif method == "SVR":
    model = SVR()
  search = GridSearchCV(estimator=model, param_grid=param_grid, scoring=scoring, cv=10, refit=False, n_jobs=-1)
  if mode == "grid_search":
    search = GridSearchCV(estimator=model, param_grid=param_grid, scoring=scoring, cv=10, refit=False, n_jobs=-1)
  elif mode == "random_search":
    pass
    search = RandomizedSearchCV(estimator=model, param_distributions=param_grid, scoring=scoring, cv=5, n_iter=10000, refit=False, n_jobs=-1)
  search.fit(X_train, y_train)
  return search

In [ ]:
import pandas as pd
df = pd.read_csv("fluvacc metadata - UGA1-5 - 1368 entries with clear vacc status - for figures.txt", sep="\t")  ##TODO: put the name of the file here
train_df, test_df = basic_preprocessing2(df, normalize=True)
train_df.to_csv("new_train.csv",sep="\t")
test_df.to_csv("new_test.csv", sep="\t")
#model_name_list = ["LOGR","SGDC", "RFC", "SVC", "KNNC"]
model_name_list = ["LOGR", "SGDC", "RFC", "SVC"]

X_trains, y_trains, X_tests, y_tests = dataset_wrapper(train_df, test_df, 
                                                  input_columns=["Age_log", "BMI_log", 
                                                                  "BMI_category", "Gender_Male", 
                                                                  "Race_White", "Comorbidities", 
                                                                  "PreVacc_status_year", "Vaccine_dose", 
                                                                  "D0_Titer_H1N1", "D0_Titer_H3N2", 
                                                                  "D0_Titer_IBV_Yam", "D0_Titer_IBV_Vic", 
                                                                  "Month_vaccinated_Jan.","Month_vaccinated_Feb.", 
                                                                  "Month_vaccinated_Sep.", "Month_vaccinated_Oct.", 
                                                                  "Month_vaccinated_Nov."], 
                                                  output_column= "Composite_SC_category",
                                                  split_age=False,
                                                  split_age_test=False)

param_grid_dict = {"LOGR": 
              {"penalty": ("l1", "l2", "elasticnet", "none"),
               "dual": (False, True), 
               "C": (1e-3, 5e-3, 1e-2, 5e-2, 0.1, 0.5, 1, 5, 10), 
               "intercept_scaling": (0, 0,5, 1, 5), 
               "solver": ("newton-cg", "lbfgs", "liblinear", "sag", "saga"), 
               "l1_ratio": (0, 0.15, 0.3, 0.45, 0.6, 0.75, 0.9, 1.0)},
              "KNNC":
              {"n_neighbors": (3, 5, 7, 10),
               "weights": ("uniform", "distance"),
               "algorithm": ("auto", "ball_tree", "kd_tree", "brute"),
               "leaf_size": (10, 20, 30, 40, 50, 100),
               "p": (1, 2, 3),
               "metric": ("chebyshev", "minkowski", "seuclidean", "mahalanobis"),
               "metric_params": ({"w": 1}, {"w": 2}, {"w": 3}, {"V": 1}, {"V": 2}, {"V": 3})},
              "SGDC":
              {"penalty": ("l2", "l1", "elasticnet"),
               "loss": ("squared_error", "hinge", "log", "modified_huber", "squared_hinge", "perceptron"),
               "alpha": (1e-6, 1e-5, 1e-4, 1e-3, 0.01, 0.1, 1),
               "l1_ratio": (0, 0.15, 0.3, 0.45, 0.6, 0.75, 0.9, 1.0),
               "epsilon": (0.1,0.2, 0.3, 0.5, 0.7, 0.9),
               "learning_rate": ("optimal", "invscaling", "constant", "adaptive"),
               "eta0": (1e-5, 1e-5, 1e-4, 1e-3, 1e-2, 0.1),
               "power_t": (0.1, 0.25, 0.5, 0.57, 0.9),
               "average": (False, True)},
              "RFC":
              {"n_estimators": (10, 25, 50, 75, 100), 
               "criterion": ("gini", "entropy"), 
               "max_depth": (None, 10, 100, 1000),
               "min_samples_split": (2, 5, 10),
               "min_samples_leaf": (1, 2, 5),
               "min_weight_fraction_leaf": (0.0, 1.0, 5.0, 10.0),
               "max_features": ("auto", "sqrt", "log2"),
               "max_leaf_nodes": (None, 10, 50, 100, 200, 500, 1000),
               "min_impurity_decrease": (0.0, 0.5, 1.0, 5.0, 10.0),
               "bootstrap": (True, False),
               "oob_score": (True, False),
               "ccp_alpha": (0.0, 1e-5, 1e-4, 1e-3, 1e-2, 0.1, 1),
               "max_samples": (None, 0.1, 0.25, 0.5, 0.75, 0.9, 1.0)},
              "SVC":
              {"C": (1e-3, 5e-3, 1e-2, 5e-2, 0.1, 0.5, 1, 5, 10), 
               "kernel": ("rbf", "linear", "poly", "sigmoid"),
               "degree": (1, 2, 3, 4, 5),
               "gamma": ("scale", "auto"),
               "coef0": (0.0,1e-3, 1e-2, 0.1, 1, 5, 10),
               "shrinking": (True, False),
               "probability": (True, False),
               "decision_function_shape": ("ovr", "ovo"),
               "break_ties": (False, True)}
              }

for model_name in model_name_list:
  for i in range(len(X_trains)):
    print(model_name)
    search = cv_wrapper(X_trains[i], y_trains[i], model_name, param_grid_dict[model_name], ["accuracy", "average_precision", "f1", "precision", "recall", "roc_auc"],mode="random_search")
    df = pd.concat([pd.DataFrame(search.cv_results_["params"]), 
                    pd.DataFrame(search.cv_results_["mean_test_accuracy"], columns=["accuracy"]), 
                    pd.DataFrame(search.cv_results_["mean_test_average_precision"], columns=["average_precision"]),
                    pd.DataFrame(search.cv_results_["mean_test_f1"], columns=["f1"]),
                    pd.DataFrame(search.cv_results_["mean_test_precision"], columns=["precision"]), 
                    pd.DataFrame(search.cv_results_["mean_test_recall"], columns=["recall"]),
                    pd.DataFrame(search.cv_results_["mean_test_roc_auc"], columns=["roc_auc"])], axis=1)
    df.to_csv(model_name+ "3.csv", sep="\t")

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


LOGR


/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_validation.py:372: FitFailedWarning: 
35205 fits failed out of a total of 50000.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
5005 fits failed with the following error:
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_validation.py", line 680, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py", line 1461, in fit
    solver = _check_solver(self.solver, self.penalty, self.dual)
  File "/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_logistic.py", line 453, in _check_solver
    "Solver %s supports only dual=

SGDC
RFC


/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_validation.py:372: FitFailedWarning: 
43150 fits failed out of a total of 50000.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
21210 fits failed with the following error:
Traceback (most recent call last):
  File "/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_validation.py", line 680, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/usr/local/lib/python3.7/dist-packages/sklearn/ensemble/_forest.py", line 380, in fit
    "`max_sample` cannot be set if `bootstrap=False`. "
ValueError: `max_sample` cannot be set if `bootstrap=False`. Either switch to `bootstrap=True` or set `max_sample=None`.

-------------------------------------

SVC


/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_search.py:972: UserWarning: One or more of the test scores are non-finite: [0.85458087        nan 0.75868627 ...        nan 0.77055842 0.75868627]
  category=UserWarning,
/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_search.py:972: UserWarning: One or more of the test scores are non-finite: [0.7612212         nan 0.74318383 ...        nan 0.58320031 0.66894442]
  category=UserWarning,
/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_search.py:972: UserWarning: One or more of the test scores are non-finite: [0.56659914        nan 0.         ...        nan 0.10385865 0.        ]
  category=UserWarning,
/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_search.py:972: UserWarning: One or more of the test scores are non-finite: [0.86081323        nan 0.         ...        nan 0.66666667 0.        ]
  category=UserWarning,
/usr/local/lib/python3.7/dist-packages/sklearn/model_selecti

The results of CV will be shown in the subsequent notebook.